<a href="https://colab.research.google.com/github/kkb0318/benkyokai/blob/main/random_forest.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Install

In [12]:
!apt-get install python-pydot
!pip install pydotplus
! pip install dtreeviz

Reading package lists... Done
Building dependency tree       
Reading state information... Done
python-pydot is already the newest version (1.2.3-1).
0 upgraded, 0 newly installed, 0 to remove and 29 not upgraded.
     |████████████████████████████████| 51kB 2.7MB/s 
  Created wheel for dtreeviz: filename=dtreeviz-1.1.4-cp37-none-any.whl size=53568 sha256=ef4e66663633eb354c453e1247198ff5c1472947a018ea3490ccb05434294f00
  Stored in directory: /root/.cache/pip/wheels/6a/1b/01/8d804e4d3cf01cf38097a756b02c851a032c09e3a25feb7c50
Successfully built dtreeviz


## titanic dataset

In [2]:
import numpy as np
import pandas as pd
from IPython.display import clear_output
from matplotlib import pyplot as plt

# Load dataset.
dftrain = pd.read_csv('https://storage.googleapis.com/tf-datasets/titanic/train.csv')
dfeval = pd.read_csv('https://storage.googleapis.com/tf-datasets/titanic/eval.csv')
y_train = dftrain.pop('survived')
y_eval = dfeval.pop('survived')




<table>
  <tr>
    <th>Feature Name</th>
    <th>Description</th>
  </tr>
  <tr>
    <td>sex</td>
    <td>Gender of passenger</td>
  </tr>
  <tr>
    <td>age</td>
    <td>Age of passenger</td>
  </tr>
    <tr>
    <td>n_siblings_spouses</td>
    <td>siblings and partners aboard</td>
  </tr>
    <tr>
    <td>parch</td>
    <td>of parents and children aboard</td>
  </tr>
    <tr>
    <td>fare</td>
    <td>Fare passenger paid.</td>
  </tr>
    <tr>
    <td>class</td>
    <td>Passenger's class on ship</td>
  </tr>
    <tr>
    <td>deck</td>
    <td>Which deck passenger was on</td>
  </tr>
    <tr>
    <td>embark_town</td>
    <td>Which town passenger embarked from</td>
  </tr>
    <tr>
    <td>alone</td>
    <td>If passenger was alone</td>
  </tr>
</table>

In [3]:
dftrain.head()

sex   age  n_siblings_spouses  parch  ...  class     deck  embark_town alone
0    male  22.0                   1      0  ...  Third  unknown  Southampton     n
1  female  38.0                   1      0  ...  First        C    Cherbourg     n
2  female  26.0                   0      0  ...  Third  unknown  Southampton     y
3  female  35.0                   1      0  ...  First        C  Southampton     n
4    male  28.0                   0      0  ...  Third  unknown   Queenstown     y

[5 rows x 9 columns]

## Train and evaluate the model

### Preprocessing

In [4]:
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestClassifier

In [5]:
def make_input_fn(X):
  #print(X.isnull().sum())
  X = X.dropna()
  X["sex"] = X["sex"].map({"male":0,"female":1})
  X["alone"] = X["alone"].map({"n":0,"y":1})
  X = pd.get_dummies(X, columns=['embark_town'])
  X = pd.get_dummies(X, columns=['class'])
  X = pd.get_dummies(X, columns=['deck'])
  return X

In [6]:
x_train = make_input_fn(dftrain)
x_eval = make_input_fn(dfeval)

In [7]:
# 足りない列を追加
x_eval[x_train.columns.difference(x_eval.columns)]=0
x_eval

sex   age  n_siblings_spouses  parch  ...  deck_E  deck_F  deck_unknown  deck_G
0      0  35.0                   0      0  ...       0       0             1       0
1      0  54.0                   0      0  ...       1       0             0       0
2      1  58.0                   0      0  ...       0       0             0       0
3      1  55.0                   0      0  ...       0       0             1       0
4      0  34.0                   0      0  ...       0       0             0       0
..   ...   ...                 ...    ...  ...     ...     ...           ...     ...
259    1  25.0                   0      1  ...       0       0             1       0
260    0  33.0                   0      0  ...       0       0             1       0
261    1  39.0                   0      5  ...       0       0             1       0
262    0  27.0                   0      0  ...       0       0             1       0
263    0  26.0                   0      0  ...       0       0             0       0

[264 rows x 21 columns]

### Training

In [8]:
clf = RandomForestClassifier(random_state=42,n_estimators=100, max_features=1).fit(x_train, y_train)

In [9]:
predicted = clf.predict(x_eval)

### evaluation

In [10]:
from sklearn.metrics import confusion_matrix, precision_score
print(confusion_matrix(y_eval,predicted))
print(precision_score(y_eval,predicted))

[[129  36]
 [ 23  76]]
0.6785714285714286


## Visualization

In [21]:
from dtreeviz.trees import dtreeviz
viz = dtreeviz(
    clf.estimators_[0],
    x_eval, 
    y_eval,
    target_name='survived',
    feature_names=x_eval.columns.values.tolist(),
) 

viz

/usr/local/lib/python3.7/dist-packages/numpy/core/_asarray.py:83: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order)
/usr/local/lib/python3.7/dist-packages/dtreeviz/trees.py:999: UserWarning: Attempting to set identical left == right == 0.0 results in singular transformations; automatically expanding.
  ax.set_xlim(*overall_feature_range_wide)
findfont: Font family ['Arial'] not found. Falling back to DejaVu Sans.
